### To create train dataset, we use already existing registered and unstained 1024 x 1024 tiles. Since our US tiles are already registered to the dimensions of HE, they should have similar coordinates to the HE mask, the only problem is the resolution difference. Let's tackle this problem by using the known rescale factor or rsf by dividing the WSI image size by the mask size, which happens to be ~9. Then, the masks created have the size 113 x 113 (1024/9.07), and then we resize the masks using nearest neighbor to make it 1024 x 1024.

In [2]:
import numpy as np
import os
from PIL import Image
Image.MAX_IMAGE_PIXELS = None
import cv2
from natsort import natsorted
import os
from matplotlib import pyplot as plt
from skimage.color import rgb2gray
from skimage.transform import warp
from skimage.registration import optical_flow_tvl1, optical_flow_ilk
import xml.etree.ElementTree as ET
import pandas as pd
import skimage.measure
import scipy.stats as stats
import time
import shutil
from tqdm import tqdm
from skimage.measure import label, regionprops_table
from natsort import natsorted

In [3]:
unstained_registered_tile_src = r"\\shelter\Kyu\unstain2stain\tiles\registered_tiles\US"
label_mask_src = r"\\shelter\Kyu\unstain2stain\unstain2stain_wsi\HE\1um\classification_v9_combined"
label_mask_list = [x for x in os.listdir(label_mask_src) if x.endswith(".png")]
label_mask_list = [x for x in label_mask_list if x[:3] == "OTS"]
label_mask_list = label_mask_list[2:]
del(label_mask_list[7]) # remove 'OTS_14684_9 and 5 _he.png', poorly registrated
del(label_mask_list[3])
label_mask_list = natsorted(label_mask_list)
label_mask_name_list = [x.replace(".png","") for x in label_mask_list]
label_mask_name_list = [x.replace("_he","") for x in label_mask_name_list]
label_mask_src = [os.path.join(label_mask_src,x) for x in label_mask_list]
unstained_registered_tile_src = [os.path.join(unstained_registered_tile_src,x) for x in label_mask_name_list]

In [4]:
label_mask_name_list

['OTS_14684_1',
 'OTS_14684_2',
 'OTS_14684_3',
 'OTS_14684_6',
 'OTS_14684_7',
 'OTS_14684_8',
 'OTS_14832_1',
 'OTS_14832_2',
 'OTS_14832_5',
 'OTS_14832_8',
 'OTS_14832_9',
 'OTS_14832_10',
 'OTS_14832_11',
 'OTS_14832_12',
 'OTS_14832_13',
 'OTS_14832_14',
 'OTS_14832_15',
 'OTS_14832_16']

In [5]:
label_mask_src

['\\\\shelter\\Kyu\\unstain2stain\\unstain2stain_wsi\\HE\\1um\\classification_v9_combined\\OTS_14684_1_he.png',
 '\\\\shelter\\Kyu\\unstain2stain\\unstain2stain_wsi\\HE\\1um\\classification_v9_combined\\OTS_14684_2_he.png',
 '\\\\shelter\\Kyu\\unstain2stain\\unstain2stain_wsi\\HE\\1um\\classification_v9_combined\\OTS_14684_3_he.png',
 '\\\\shelter\\Kyu\\unstain2stain\\unstain2stain_wsi\\HE\\1um\\classification_v9_combined\\OTS_14684_6_he.png',
 '\\\\shelter\\Kyu\\unstain2stain\\unstain2stain_wsi\\HE\\1um\\classification_v9_combined\\OTS_14684_7_he.png',
 '\\\\shelter\\Kyu\\unstain2stain\\unstain2stain_wsi\\HE\\1um\\classification_v9_combined\\OTS_14684_8_he.png',
 '\\\\shelter\\Kyu\\unstain2stain\\unstain2stain_wsi\\HE\\1um\\classification_v9_combined\\OTS_14832_1_he.png',
 '\\\\shelter\\Kyu\\unstain2stain\\unstain2stain_wsi\\HE\\1um\\classification_v9_combined\\OTS_14832_2_he.png',
 '\\\\shelter\\Kyu\\unstain2stain\\unstain2stain_wsi\\HE\\1um\\classification_v9_combined\\OTS_14832_5_h

In [6]:
unstained_registered_tile_src

['\\\\shelter\\Kyu\\unstain2stain\\tiles\\registered_tiles\\US\\OTS_14684_1',
 '\\\\shelter\\Kyu\\unstain2stain\\tiles\\registered_tiles\\US\\OTS_14684_2',
 '\\\\shelter\\Kyu\\unstain2stain\\tiles\\registered_tiles\\US\\OTS_14684_3',
 '\\\\shelter\\Kyu\\unstain2stain\\tiles\\registered_tiles\\US\\OTS_14684_6',
 '\\\\shelter\\Kyu\\unstain2stain\\tiles\\registered_tiles\\US\\OTS_14684_7',
 '\\\\shelter\\Kyu\\unstain2stain\\tiles\\registered_tiles\\US\\OTS_14684_8',
 '\\\\shelter\\Kyu\\unstain2stain\\tiles\\registered_tiles\\US\\OTS_14832_1',
 '\\\\shelter\\Kyu\\unstain2stain\\tiles\\registered_tiles\\US\\OTS_14832_2',
 '\\\\shelter\\Kyu\\unstain2stain\\tiles\\registered_tiles\\US\\OTS_14832_5',
 '\\\\shelter\\Kyu\\unstain2stain\\tiles\\registered_tiles\\US\\OTS_14832_8',
 '\\\\shelter\\Kyu\\unstain2stain\\tiles\\registered_tiles\\US\\OTS_14832_9',
 '\\\\shelter\\Kyu\\unstain2stain\\tiles\\registered_tiles\\US\\OTS_14832_10',
 '\\\\shelter\\Kyu\\unstain2stain\\tiles\\registered_tiles\\US\

In [7]:
def calculate_offset(string):
    x1 = int(string.split("-")[0].split(" ")[0].split("[")[1])
    y1 = int(string.split("-")[0].split(" ")[1].split("]")[0])
    x2 = int(string.split("-")[1].split(" ")[1].split("[")[1])
    y2 = int(string.split("-")[1].split(" ")[2].split("]")[0])
    offset_x = x1 - x2
    offset_y = y1 - y2
    return (offset_x,offset_y)

offset_df_src = r"\\shelter\Kyu\unstain2stain\unstain2stain_wsi\wsi_list_230314.xlsx"
offset_df = pd.read_excel(offset_df_src)
offset_list = offset_df["offNSHE"].tolist()
offset_list = [x for x in offset_list if not isinstance(x,float)] #drop nan's
offset_list = [calculate_offset(x) for x in offset_list]
offset_list1 = []
for x in offset_list:
    if x not in offset_list1:
        offset_list1.append(x)

# delete the five images not used:
del offset_list1[15]
del offset_list1[14]
del offset_list1[12]
del offset_list1[11]
del offset_list1[4]
del offset_list1[3]


In [8]:
offset_list1

[(7675, -3411),
 (10441, 5631),
 (43804, 15479),
 (-10960, 3890),
 (27057, -6216),
 (35227, -1078),
 (-237, 4174),
 (24229, 19948),
 (47104, 3372),
 (35241, 3112),
 (23660, 2693),
 (34692, 19307),
 (44896, 4143),
 (41703, -1029),
 (81283, 13046),
 (35934, -1849),
 (21458, 14631),
 (31229, 15865),
 (54735, 7436)]

In [9]:
len(offset_list1)

19

In [9]:
# ### Let's first test the first WSI image:
# masksrc = label_mask_src[0]
# mask = Image.open(masksrc)
# maskra = np.array(mask)
# print(maskra.shape) # height x width (W x H in imagej and ndpi's)
# rsf = 9.0769 # this is the difference in size b/w the ndpi (the tiles are from ndpi so we have to look at ndpi 40x dimension) and the mask
# tile_size = round(1024/rsf)
# # Test the HE image "\\shelter\Kyu\unstain2stain\tiles\registered_tiles\HE\OTS_14684_1_he\37990_12390xy3324.png" to see if the mask does contain the right composition
# x,y = (41062,27750) # US x,y - offsetlist x,y = HE x,y, need to use HE x,y.
# x = round(x/rsf)
# y = round(y/rsf)
# corresp_mask = maskra[y:y+tile_size,x:x+tile_size]
# save corresp_mask and view!
### It works pretty well! Let's now run over all tiles and create the entire dataset:

In [10]:
rsf = 9.0769 # this is the difference in size b/w the ndpi (the tiles are from ndpi so we have to look at ndpi 40x dimension) and the mask
rsf_tile_size = round(1024/rsf)
dst_src = r'\\shelter\Kyu\unstain2mask\masks'

In [11]:
for wsi_idx in tqdm(range(len(label_mask_src)),colour='red',desc="WSIs Processed",total=len(label_mask_src)):
    label_mask = Image.open(label_mask_src[wsi_idx])
    label_mask = np.array(label_mask)
    US_tile_src = unstained_registered_tile_src[wsi_idx]
    all_tile_src = os.listdir(US_tile_src)
    all_tile_save_src = [os.path.join(US_tile_src,x) for x in all_tile_src if x.endswith(".png")]
    offset = offset_list1[wsi_idx]
    offset_x = offset[0]
    offset_y = offset[1]
    wsi_name = label_mask_name_list[wsi_idx]
    mask_save_src = os.path.join(dst_src,wsi_name)
    print("label mask size is",label_mask.shape)
    if not os.path.exists(mask_save_src):
        os.makedirs(mask_save_src)
    if os.path.exists(mask_save_src) and len(os.listdir(mask_save_src)) == len(all_tile_save_src):
        print("Mask for {} already made".format(wsi_name))
        continue
    print("Processing {}".format(wsi_name))
    for tile_idx in tqdm(range(len(all_tile_save_src)),colour='red',desc="Tiles Processed",total=len(all_tile_save_src)):
        tile_src = all_tile_save_src[tile_idx]
        tile = Image.open(tile_src)
        tile = np.array(tile)
        us_x = int(tile_src.split("xy")[0].split("\\")[-1].split("_")[0])
        us_y = int(tile_src.split("xy")[0].split("\\")[-1].split("_")[1])
        he_x = us_x - offset_x
        he_y = us_y - offset_y
        rsf_x = round(he_x/rsf)
        rsf_y = round(he_y/rsf)
        corresp_mask = label_mask[rsf_y:rsf_y+rsf_tile_size,rsf_x:rsf_x+rsf_tile_size]
        tile_save_src = os.path.join(mask_save_src,all_tile_src[tile_idx])
        try:
            Image.fromarray(corresp_mask).save(tile_save_src)
        except:
            continue

WSIs Processed:   0%|          | 0/18 [00:00<?, ?it/s]

label mask size is (10548, 16499)


WSIs Processed:   6%|▌         | 1/18 [00:13<03:56, 13.90s/it]

Mask for OTS_14684_1 already made
label mask size is (9307, 14384)


WSIs Processed:  11%|█         | 2/18 [00:26<03:29, 13.12s/it]

...


WSIs Processed:  89%|████████▉ | 16/18 [1:41:12<19:14, 577.47s/it]

label mask size is (10548, 16499)
Processing OTS_14832_15



WSIs Processed:  94%|█████████▍| 17/18 [1:52:47<10:12, 612.82s/it]

label mask size is (9617, 8884)
Processing OTS_14832_16



WSIs Processed: 100%|██████████| 18/18 [1:53:58<00:00, 379.90s/it]


In [11]:
# Now resize all the masks to 1024 x 1024 (113 x 113 original size):
masksrc = r"\\shelter\Kyu\unstain2mask\masks"
masklist = os.listdir(masksrc)
masklist_src = [os.path.join(masksrc,x) for x in masklist]
for mask_idx in tqdm(range(len(masklist_src)),colour='red',desc="WSIs Processed"):
    wsi_mask = masklist_src[mask_idx]
    masks_list = os.listdir(wsi_mask)
    masks_name = [x for x in masks_list if x.endswith(".png")]
    wsi_name = os.path.basename(wsi_mask)
    test_dst_dir = os.path.join(masksrc,wsi_name)
    if not os.path.exists(test_dst_dir):
        os.makedir(test_dst_dir)
    if os.path.exists(test_dst_dir) and len(os.listdir(test_dst_dir)) == len(masks_name):
        print("Already exists, continuing to next WSI")
        continue
    for idx in tqdm(range(len(masks_name)),colour='red',desc="Masks Processed"):
        mask = Image.open(os.path.join(wsi_mask,masks_name[idx]))
        mask_ra = np.array(mask)
        resize_mask = cv2.resize(mask_ra,dsize = (1024,1024), interpolation = 0)
        dst_dir = os.path.join(test_dst_dir,masks_name[idx])
        Image.fromarray(resize_mask).save(dst_dir)

WSIs Processed:   5%|▌         | 1/19 [00:01<00:25,  1.39s/it]

Already exists, continuing to next WSI


WSIs Processed:  11%|█         | 2/19 [00:02<00:23,  1.38s/it]

Already exists, continuing to next WSI


WSIs Processed:  16%|█▌        | 3/19 [00:03<00:19,  1.20s/it]

...

Already exists, continuing to next WSI


WSIs Processed:  95%|█████████▍| 18/19 [00:18<00:01,  1.06s/it]

Already exists, continuing to next WSI


WSIs Processed: 100%|██████████| 19/19 [00:19<00:00,  1.02s/it]

Already exists, continuing to next WSI
